In [1]:
import jieba,os,re
from gensim import corpora, models, similarities
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

from sklearn import preprocessing
from sklearn import metrics
from sklearn.linear_model import LogisticRegression
from sklearn import svm
from sklearn.neural_network import MLPClassifier
from keras.layers import LSTM
from keras.layers import GRU
from keras.layers import Bidirectional

from sklearn.model_selection import cross_validate, train_test_split
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, classification_report
from sklearn.model_selection import KFold

from keras.callbacks import EarlyStopping
from keras.models import Sequential
from keras.layers import SimpleRNN, Dense
max_abs_scaler = preprocessing.MaxAbsScaler()


def getPositionEncoding(seq_len, d, n):
    P = np.zeros((seq_len, d))
    for k in range(seq_len):
        for i in np.arange(int(d/2)):
            denominator = np.power(n, 2*i/d)
            P[k, 2*i] = np.sin(k/denominator)
            P[k, 2*i+1] = np.cos(k/denominator)
    return P

def getPositionEmbedding(column_name, short_name, d, n=10000):
    seq_len = merge_pd[column_name].max()
    result = getPositionEncoding(seq_len, d, n)
    df_PE = pd.DataFrame(result)
    df_PE.index = np.arange(1, len(df_PE) + 1)

    df_PE.index.name = column_name
    column_names = []

    for i in range(d):
        column_names.append(short_name + '_' + str(i + 1))
    df_PE.columns = column_names
    return df_PE


# LR

In [4]:
# LR rank
LR_results = []

for d in range(5, 1000, 10):

    input_df=pd.read_csv('Student Engagement Level Prediction - Multiclass Case/Student Engagement Level-Multiclass.csv')
    input_p_df=pd.read_csv('Student Performance Prediction - Multiclass Case/Student Performance Prediction-Multi.csv')
    merge_pd = pd.merge(input_df, input_p_df, on='Student ID')

    ''' creat columns called 'Assignment0x [n]_rank' for different assignments '''

    merge_pd['Assignment01 [8]_rank'] = merge_pd['Assignment01 [8]'].rank(ascending=False, method='max').astype(int)
    merge_pd['Assignment02 [12]_rank'] = merge_pd['Assignment02 [12]'].rank(ascending=False, method='max').astype(int)
    merge_pd['Assignment03 [25]_rank'] = merge_pd['Assignment03 [25]'].rank(ascending=False, method='max').astype(int)

    # get the position embedding for each assignment
    df_1 = pd.DataFrame(getPositionEmbedding('Assignment01 [8]_rank', 'A1', d))
    df_2 = pd.DataFrame(getPositionEmbedding('Assignment02 [12]_rank', 'A2', d))
    df_3 = pd.DataFrame(getPositionEmbedding('Assignment03 [25]_rank', 'A3', d))

    # define label
    merge_pd['below 70'] = 0
    merge_pd.loc[merge_pd['Course Grade']<70, 'below 70'] = 1

    # merge the position embedding with the original data
    merge_pd = pd.merge(pd.merge(pd.merge(merge_pd, df_1, on='Assignment01 [8]_rank'), df_2, on='Assignment02 [12]_rank'), df_3, on='Assignment03 [25]_rank')

    col1 =[]
    col2 = []
    col3 = []
    col_all = []

    col1 = df_1.columns.tolist()
    col2 = df_2.columns.tolist()
    col3 = df_3.columns.tolist()

    col_all = np.concatenate([col1, col2, col3])

    ## LR rank
    # Define feature set and target variable
    X = np.array(merge_pd[col_all])
    X = max_abs_scaler.fit_transform(X) 
    Y = np.array(merge_pd['below 70'])

    # Transfer the SVM model into Logistic Regression model
    model = LogisticRegression(max_iter= 5000)

    # Evaluate the model using 5-fold cross-validation
    scoring = ['accuracy', 'precision_macro', 'recall_macro', 'f1_macro']
    cv_results = cross_validate(model, X, Y, cv=5, scoring=scoring)

    # # Print the average performance across all folds
    # print("Accuracy:", np.mean(cv_results['test_accuracy']))
    # print("Precision:", np.mean(cv_results['test_precision_macro']))
    # print("Recall:", np.mean(cv_results['test_recall_macro']))
    # print("F1:", np.mean(cv_results['test_f1_macro']))
    # 把平均性能指标加入到结果列表中
    LR_results.append(np.mean(cv_results['test_f1_macro']))


# 打印结果列表
print(LR_results)

c:\Users\wyzhw\Documents\GitHub\Desktop\.conda\lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\wyzhw\Documents\GitHub\Desktop\.conda\lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\wyzhw\Documents\GitHub\Desktop\.conda\lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\wyzhw\Documents\Git

[0.48427696398893777, 0.6160155227418627, 0.614660242138289, 0.5735985578687709, 0.5317951401231993, 0.5278911398379098, 0.557663249526227, 0.5297696900816957, 0.5271031248119078, 0.5183188575488086, 0.5527614467120511, 0.5097254633212771, 0.5215368535469074, 0.5021474631364393, 0.5044679721718808, 0.5149495581318329, 0.5270068042793861, 0.506329618895554, 0.5085864311108275, 0.500900566581164, 0.5140983882933451, 0.5131235497958165, 0.5175962581899655, 0.516087575307828, 0.5175423527077971, 0.5081492202240393, 0.5109700722205994, 0.5189611824608287, 0.5001948093252317, 0.5003240381358512, 0.5139993208383482, 0.5183981635912813, 0.5056177558285626, 0.5065670738609842, 0.500752322238036, 0.49258333910961377, 0.5206176756598013, 0.5152311208785175, 0.5080339363296792, 0.5042158593405086, 0.5046473321514261, 0.5091165594680481, 0.5027050223606433, 0.5158879697723846, 0.5138386186177447, 0.5166055096779859, 0.5174596943201859, 0.5164128221573753, 0.5102273343380874, 0.5125025709150945, 0.5

# SVM

In [5]:
# SVM rank

SVM_results = []

for d in range(5, 1000, 10):

    input_df=pd.read_csv('Student Engagement Level Prediction - Multiclass Case/Student Engagement Level-Multiclass.csv')
    input_p_df=pd.read_csv('Student Performance Prediction - Multiclass Case/Student Performance Prediction-Multi.csv')
    merge_pd = pd.merge(input_df, input_p_df, on='Student ID')

    ''' creat columns called 'Assignment0x [n]_rank' for different assignments '''

    merge_pd['Assignment01 [8]_rank'] = merge_pd['Assignment01 [8]'].rank(ascending=False, method='max').astype(int)
    merge_pd['Assignment02 [12]_rank'] = merge_pd['Assignment02 [12]'].rank(ascending=False, method='max').astype(int)
    merge_pd['Assignment03 [25]_rank'] = merge_pd['Assignment03 [25]'].rank(ascending=False, method='max').astype(int)

    # get the position embedding for each assignment
    df_1 = pd.DataFrame(getPositionEmbedding('Assignment01 [8]_rank', 'A1', d))
    df_2 = pd.DataFrame(getPositionEmbedding('Assignment02 [12]_rank', 'A2', d))
    df_3 = pd.DataFrame(getPositionEmbedding('Assignment03 [25]_rank', 'A3', d))

    # define label
    merge_pd['below 70'] = 0
    merge_pd.loc[merge_pd['Course Grade']<70, 'below 70'] = 1

    # merge the position embedding with the original data
    merge_pd = pd.merge(pd.merge(pd.merge(merge_pd, df_1, on='Assignment01 [8]_rank'), df_2, on='Assignment02 [12]_rank'), df_3, on='Assignment03 [25]_rank')

    col1 =[]
    col2 = []
    col3 = []
    col_all = []

    col1 = df_1.columns.tolist()
    col2 = df_2.columns.tolist()
    col3 = df_3.columns.tolist()

    col_all = np.concatenate([col1, col2, col3])

    ## LR rank
    # Define feature set and target variable
    X = np.array(merge_pd[col_all])
    X = max_abs_scaler.fit_transform(X) 
    Y = np.array(merge_pd['below 70'])
    
    # Transfer to the SVM model 
    model = svm.SVC(kernel='rbf',decision_function_shape='ovo')

    # Evaluate the model using 5-fold cross-validation
    scoring = ['accuracy', 'precision_macro', 'recall_macro', 'f1_macro']
    cv_results = cross_validate(model, X, Y, cv=5, scoring=scoring)

    # # Print the average performance across all folds
    # print("Accuracy:", np.mean(cv_results['test_accuracy']))
    # print("Precision:", np.mean(cv_results['test_precision_macro']))
    # print("Recall:", np.mean(cv_results['test_recall_macro']))
    # print("F1:", np.mean(cv_results['test_f1_macro']))
    # 把平均性能指标加入到结果列表中
    SVM_results.append(np.mean(cv_results['test_f1_macro']))

# 打印结果列表
print(SVM_results)

c:\Users\wyzhw\Documents\GitHub\Desktop\.conda\lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\wyzhw\Documents\GitHub\Desktop\.conda\lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\wyzhw\Documents\GitHub\Desktop\.conda\lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\wyzhw\Documents\Git

[0.4740451105352599, 0.5747908686186853, 0.5941845672469904, 0.5906968688983744, 0.5961515995662889, 0.588880164440492, 0.5970540418948508, 0.5900741159451129, 0.5964312889415894, 0.5937151883452708, 0.6042991392619229, 0.5937151883452708, 0.5958014188117191, 0.5944166941208573, 0.5944166941208573, 0.5924420894466778, 0.5937151883452708, 0.5944166941208573, 0.5944166941208573, 0.593786823990987, 0.5944166941208573, 0.5958014188117191, 0.5924420894466778, 0.5944166941208573, 0.5944166941208573, 0.5944166941208573, 0.5924420894466778, 0.5964312889415894, 0.593786823990987, 0.5944166941208573, 0.5924420894466778, 0.5918122193168076, 0.5944166941208573, 0.5944166941208573, 0.593786823990987, 0.5924420894466778, 0.5944166941208573, 0.5924420894466778, 0.593786823990987, 0.5918122193168076, 0.5944166941208573, 0.5924420894466778, 0.5918122193168076, 0.5918122193168076, 0.5944166941208573, 0.5944166941208573, 0.593786823990987, 0.5944166941208573, 0.5918122193168076, 0.593786823990987, 0.5937

# MLP

In [6]:
# MLP rank

MLP_results = []

for d in range(5, 1000, 10):
    input_df=pd.read_csv('Student Engagement Level Prediction - Multiclass Case/Student Engagement Level-Multiclass.csv')
    input_p_df=pd.read_csv('Student Performance Prediction - Multiclass Case/Student Performance Prediction-Multi.csv')
    merge_pd = pd.merge(input_df, input_p_df, on='Student ID')

    ''' creat columns called 'Assignment0x [n]_rank' for different assignments '''

    merge_pd['Assignment01 [8]_rank'] = merge_pd['Assignment01 [8]'].rank(ascending=False, method='max').astype(int)
    merge_pd['Assignment02 [12]_rank'] = merge_pd['Assignment02 [12]'].rank(ascending=False, method='max').astype(int)
    merge_pd['Assignment03 [25]_rank'] = merge_pd['Assignment03 [25]'].rank(ascending=False, method='max').astype(int)

    # get the position embedding for each assignment
    df_1 = pd.DataFrame(getPositionEmbedding('Assignment01 [8]_rank', 'A1', d))
    df_2 = pd.DataFrame(getPositionEmbedding('Assignment02 [12]_rank', 'A2', d))
    df_3 = pd.DataFrame(getPositionEmbedding('Assignment03 [25]_rank', 'A3', d))

    # define label
    merge_pd['below 70'] = 0
    merge_pd.loc[merge_pd['Course Grade']<70, 'below 70'] = 1

    # merge the position embedding with the original data
    merge_pd = pd.merge(pd.merge(pd.merge(merge_pd, df_1, on='Assignment01 [8]_rank'), df_2, on='Assignment02 [12]_rank'), df_3, on='Assignment03 [25]_rank')

    col1 =[]
    col2 = []
    col3 = []
    col_all = []

    col1 = df_1.columns.tolist()
    col2 = df_2.columns.tolist()
    col3 = df_3.columns.tolist()

    col_all = np.concatenate([col1, col2, col3])

    ## LR rank
    # Define feature set and target variable
    X = np.array(merge_pd[col_all])
    X = max_abs_scaler.fit_transform(X) 
    Y = np.array(merge_pd['below 70'])

    # Transfer into MLP model
    model = MLPClassifier(max_iter=2000) # max_iter is set to 200 as default


    # Evaluate the model using 5-fold cross-validation
    scoring = ['accuracy', 'precision_macro', 'recall_macro', 'f1_macro']
    cv_results = cross_validate(model, X, Y, cv=5, scoring=scoring)

    # # Print the average performance across all folds
    # print("Accuracy:", np.mean(cv_results['test_accuracy']))
    # print("Precision:", np.mean(cv_results['test_precision_macro']))
    # print("Recall:", np.mean(cv_results['test_recall_macro']))
    # print("F1:", np.mean(cv_results['test_f1_macro']))
    # 把平均性能指标加入到结果列表中
    MLP_results.append(np.mean(cv_results['test_f1_macro']))

# 打印结果列表
print(MLP_results)

c:\Users\wyzhw\Documents\GitHub\Desktop\.conda\lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\wyzhw\Documents\GitHub\Desktop\.conda\lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\wyzhw\Documents\GitHub\Desktop\.conda\lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\wyzhw\Documents\Git

[0.5180165749809003, 0.6165500088766199, 0.5745789201861811, 0.5712553854736668, 0.5487657926641043, 0.5533535465008479, 0.5846390600931464, 0.5483474013330822, 0.5589530877572472, 0.5450758903832144, 0.5726683653898993, 0.536214921396315, 0.5570550784155722, 0.539286364078451, 0.54379314795011, 0.556349397497313, 0.5326690140311039, 0.5476560572012744, 0.5509694553054917, 0.5402541729776807, 0.5582547860984525, 0.5523982546777852, 0.5667472225628196, 0.5677584258596626, 0.5404803831193534, 0.5448771046935651, 0.5327431948240815, 0.5416674577168031, 0.5522350876133939, 0.5556579571049252, 0.556480580742058, 0.5409160230948498, 0.5420668965455109, 0.5383131715966311, 0.5529296028079882, 0.5313559980999757, 0.5574062260515503, 0.5418826115524661, 0.5476607447867046, 0.5550726691870624, 0.5522041158284875, 0.5467658306047565, 0.555012797839349, 0.5344197037441386, 0.5487092843071987, 0.5427336536013324, 0.5534032772433319, 0.5430880516795643, 0.5464470092728935, 0.5509630813241067, 0.5397

In [7]:
SVM_results

[0.4740451105352599,
 0.5747908686186853,
 0.5941845672469904,
 0.5906968688983744,
 0.5961515995662889,
 0.588880164440492,
 0.5970540418948508,
 0.5900741159451129,
 0.5964312889415894,
 0.5937151883452708,
 0.6042991392619229,
 0.5937151883452708,
 0.5958014188117191,
 0.5944166941208573,
 0.5944166941208573,
 0.5924420894466778,
 0.5937151883452708,
 0.5944166941208573,
 0.5944166941208573,
 0.593786823990987,
 0.5944166941208573,
 0.5958014188117191,
 0.5924420894466778,
 0.5944166941208573,
 0.5944166941208573,
 0.5944166941208573,
 0.5924420894466778,
 0.5964312889415894,
 0.593786823990987,
 0.5944166941208573,
 0.5924420894466778,
 0.5918122193168076,
 0.5944166941208573,
 0.5944166941208573,
 0.593786823990987,
 0.5924420894466778,
 0.5944166941208573,
 0.5924420894466778,
 0.593786823990987,
 0.5918122193168076,
 0.5944166941208573,
 0.5924420894466778,
 0.5918122193168076,
 0.5918122193168076,
 0.5944166941208573,
 0.5944166941208573,
 0.593786823990987,
 0.5944166941208573

# RNN

In [8]:
# RNN rank

RNN_results = []

for d in range(5, 1000, 10):

    input_df=pd.read_csv('Student Engagement Level Prediction - Multiclass Case/Student Engagement Level-Multiclass.csv')
    input_p_df=pd.read_csv('Student Performance Prediction - Multiclass Case/Student Performance Prediction-Multi.csv')
    merge_pd = pd.merge(input_df, input_p_df, on='Student ID')

    ''' creat columns called 'Assignment0x [n]_rank' for different assignments '''

    merge_pd['Assignment01 [8]_rank'] = merge_pd['Assignment01 [8]'].rank(ascending=False, method='max').astype(int)
    merge_pd['Assignment02 [12]_rank'] = merge_pd['Assignment02 [12]'].rank(ascending=False, method='max').astype(int)
    merge_pd['Assignment03 [25]_rank'] = merge_pd['Assignment03 [25]'].rank(ascending=False, method='max').astype(int)

    # get the position embedding for each assignment
    df_1 = pd.DataFrame(getPositionEmbedding('Assignment01 [8]_rank', 'A1', d))
    df_2 = pd.DataFrame(getPositionEmbedding('Assignment02 [12]_rank', 'A2', d))
    df_3 = pd.DataFrame(getPositionEmbedding('Assignment03 [25]_rank', 'A3', d))

    # define label
    merge_pd['below 70'] = 0
    merge_pd.loc[merge_pd['Course Grade']<70, 'below 70'] = 1

    # merge the position embedding with the original data
    merge_pd = pd.merge(pd.merge(pd.merge(merge_pd, df_1, on='Assignment01 [8]_rank'), df_2, on='Assignment02 [12]_rank'), df_3, on='Assignment03 [25]_rank')

    col1 =[]
    col2 = []
    col3 = []
    col_all = []
    col1 = df_1.columns.tolist()
    col2 = df_2.columns.tolist()
    col3 = df_3.columns.tolist()
    col_all = np.concatenate([col1, col2, col3])

    # RNN rank
    # Define feature set and target variable
    X = np.array(merge_pd[col_all])

    X = max_abs_scaler.fit_transform(X) 
    Y = np.array(merge_pd['below 70'])


    # Reshape: Shape before reshaping: (486, 150)
    print("Shape before reshaping:", X.shape)
    X = X.reshape(X.shape[0], int(X.shape[1]/df_2.shape[1]), df_2.shape[1]) # Shape after reshaping: (486, 3, 50)
    print("Shape after reshaping:", X.shape)

    # Define the number of folds
    n_folds = 5

    # Define the KFold object
    kfold = KFold(n_splits=n_folds, shuffle=True)

    # Split data into train and test sets
    X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.5, random_state = 42)

    # Define the RNN model
    model = Sequential()
    model.add(SimpleRNN(10, input_shape=(X_train.shape[1], X_train.shape[2])))  # input_shape=(n_timesteps, features)
    model.add(Dense(1, activation='sigmoid'))  # Output layer with sigmoid activation

    # Compile the model
    model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['mae'])

    # Define early stopping criteria
    early_stopping = EarlyStopping(monitor='val_loss', patience=10, restore_best_weights=True)

    # Initialize lists to store the performance metrics
    accuracy_list = []
    precision_list = []
    recall_list = []
    f1_list = []

    # Loop over the folds
    for train_index, test_index in kfold.split(X):
        # Split data into train and test sets
        X_train, X_test = X[train_index], X[test_index]
        y_train, y_test = Y[train_index], Y[test_index]

        # Train the model
        model.fit(X_train, y_train, epochs=1024, batch_size=32, validation_data=(X_test, y_test), callbacks=[early_stopping])

        # Predict the labels for the test set
        y_pred = model.predict(X_test)
        y_pred = (y_pred > 0.5).astype(int)

        # Calculate and print the classification report
        report = classification_report(y_test, y_pred, output_dict=True)

        # Append the performance metrics to the lists
        accuracy_list.append(report['accuracy'])
        precision_list.append(report['macro avg']['precision'])
        recall_list.append(report['macro avg']['recall'])
        f1_list.append(report['macro avg']['f1-score'])
    
    RNN_results.append(np.mean(f1_list))

# 打印结果列表
print(RNN_results)

Shape before reshaping: (486, 15)
Shape after reshaping: (486, 3, 5)
Epoch 1/1024
13/13 [==============================] - 1s 22ms/step - loss: 0.7386 - mae: 0.4906 - val_loss: 0.6851 - val_mae: 0.4706
Epoch 2/1024
13/13 [==============================] - 0s 4ms/step - loss: 0.6967 - mae: 0.4753 - val_loss: 0.6559 - val_mae: 0.4600
Epoch 3/1024
13/13 [==============================] - 0s 4ms/step - loss: 0.6604 - mae: 0.4605 - val_loss: 0.6303 - val_mae: 0.4493
Epoch 4/1024
13/13 [==============================] - 0s 4ms/step - loss: 0.6273 - mae: 0.4456 - val_loss: 0.6071 - val_mae: 0.4386
Epoch 5/1024
13/13 [==============================] - 0s 4ms/step - loss: 0.5966 - mae: 0.4303 - val_loss: 0.5840 - val_mae: 0.4263
Epoch 6/1024
13/13 [==============================] - 0s 4ms/step - loss: 0.5667 - mae: 0.4140 - val_loss: 0.5629 - val_mae: 0.4138
Epoch 7/1024
13/13 [==============================] - 0s 4ms/step - loss: 0.5385 - mae: 0.3972 - val_loss: 0.5421 - val_mae: 0.4002
Epoch 

# LSTM

In [9]:
# LSTM rank

LSTM_results = []

for d in range(5, 1000, 10):
    input_df=pd.read_csv('Student Engagement Level Prediction - Multiclass Case/Student Engagement Level-Multiclass.csv')
    input_p_df=pd.read_csv('Student Performance Prediction - Multiclass Case/Student Performance Prediction-Multi.csv')
    merge_pd = pd.merge(input_df, input_p_df, on='Student ID')

    ''' creat columns called 'Assignment0x [n]_rank' for different assignments '''

    merge_pd['Assignment01 [8]_rank'] = merge_pd['Assignment01 [8]'].rank(ascending=False, method='max').astype(int)
    merge_pd['Assignment02 [12]_rank'] = merge_pd['Assignment02 [12]'].rank(ascending=False, method='max').astype(int)
    merge_pd['Assignment03 [25]_rank'] = merge_pd['Assignment03 [25]'].rank(ascending=False, method='max').astype(int)

    # get the position embedding for each assignment
    df_1 = pd.DataFrame(getPositionEmbedding('Assignment01 [8]_rank', 'A1', d))
    df_2 = pd.DataFrame(getPositionEmbedding('Assignment02 [12]_rank', 'A2', d))
    df_3 = pd.DataFrame(getPositionEmbedding('Assignment03 [25]_rank', 'A3', d))

    # define label
    merge_pd['below 70'] = 0
    merge_pd.loc[merge_pd['Course Grade']<70, 'below 70'] = 1

    # merge the position embedding with the original data
    merge_pd = pd.merge(pd.merge(pd.merge(merge_pd, df_1, on='Assignment01 [8]_rank'), df_2, on='Assignment02 [12]_rank'), df_3, on='Assignment03 [25]_rank')

    col1 =[]
    col2 = []
    col3 = []
    col_all = []
    col1 = df_1.columns.tolist()
    col2 = df_2.columns.tolist()
    col3 = df_3.columns.tolist()
    col_all = np.concatenate([col1, col2, col3])

    # LSTM rank
    # Define feature set and target variable
    X = np.array(merge_pd[col_all])

    X = max_abs_scaler.fit_transform(X) 
    Y = np.array(merge_pd['below 70'])


    # Reshape: Shape before reshaping: (486, 150)
    print("Shape before reshaping:", X.shape)
    X = X.reshape(X.shape[0], int(X.shape[1]/df_2.shape[1]), df_2.shape[1]) # Shape after reshaping: (486, 3, 50)
    print("Shape after reshaping:", X.shape)

    # Define the number of folds
    n_folds = 5

    # Define the KFold object
    kfold = KFold(n_splits=n_folds, shuffle=True)

    # Split data into train and test sets
    X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.5, random_state = 42)

    # Define the RNN model
    model = Sequential()
    #model.add(LSTM(256, dropout = 0.3, recurrent_dropout = 0.3, input_shape=(X_train.shape[1], X_train.shape[2])))
    model.add(LSTM(10, input_shape=(X_train.shape[1], X_train.shape[2])))  # input_shape=(n_timesteps, features)
    model.add(Dense(1, activation='sigmoid'))  # Output layer with sigmoid activation

    # Compile the model
    model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['mae'])

    # Define early stopping criteria
    early_stopping = EarlyStopping(monitor='val_loss', patience=10, restore_best_weights=True)

    # Initialize lists to store the performance metrics
    accuracy_list = []
    precision_list = []
    recall_list = []
    f1_list = []

    # Loop over the folds
    for train_index, test_index in kfold.split(X):
        # Split data into train and test sets
        X_train, X_test = X[train_index], X[test_index]
        y_train, y_test = Y[train_index], Y[test_index]

        # Train the model
        model.fit(X_train, y_train, epochs=4096, batch_size=32, validation_data=(X_test, y_test), callbacks=[early_stopping])

        # Predict the labels for the test set
        y_pred = model.predict(X_test)
        y_pred = (y_pred > 0.5).astype(int)

        # Calculate and print the classification report
        report = classification_report(y_test, y_pred, output_dict=True)

        # Append the performance metrics to the lists
        accuracy_list.append(report['accuracy'])
        precision_list.append(report['macro avg']['precision'])
        recall_list.append(report['macro avg']['recall'])
        f1_list.append(report['macro avg']['f1-score'])
    
    LSTM_results.append(np.mean(f1_list))

# 打印结果列表
print(LSTM_results)

Shape before reshaping: (486, 15)
Shape after reshaping: (486, 3, 5)
Epoch 1/4096
13/13 [==============================] - 2s 37ms/step - loss: 0.6670 - mae: 0.4848 - val_loss: 0.6619 - val_mae: 0.4822
Epoch 2/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.6460 - mae: 0.4735 - val_loss: 0.6438 - val_mae: 0.4722
Epoch 3/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.6240 - mae: 0.4612 - val_loss: 0.6258 - val_mae: 0.4618
Epoch 4/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.6028 - mae: 0.4489 - val_loss: 0.6074 - val_mae: 0.4507
Epoch 5/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.5805 - mae: 0.4355 - val_loss: 0.5883 - val_mae: 0.4386
Epoch 6/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.5574 - mae: 0.4209 - val_loss: 0.5697 - val_mae: 0.4262
Epoch 7/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.5337 - mae: 0.4053 - val_loss: 0.5496 - val_mae: 0.4119
Epoch 

# GRU

In [10]:
# GRU rank

GRU_results = []

for d in range(5, 1000, 10):

    input_df=pd.read_csv('Student Engagement Level Prediction - Multiclass Case/Student Engagement Level-Multiclass.csv')
    input_p_df=pd.read_csv('Student Performance Prediction - Multiclass Case/Student Performance Prediction-Multi.csv')
    merge_pd = pd.merge(input_df, input_p_df, on='Student ID')

    ''' creat columns called 'Assignment0x [n]_rank' for different assignments '''

    merge_pd['Assignment01 [8]_rank'] = merge_pd['Assignment01 [8]'].rank(ascending=False, method='max').astype(int)
    merge_pd['Assignment02 [12]_rank'] = merge_pd['Assignment02 [12]'].rank(ascending=False, method='max').astype(int)
    merge_pd['Assignment03 [25]_rank'] = merge_pd['Assignment03 [25]'].rank(ascending=False, method='max').astype(int)

    # get the position embedding for each assignment
    df_1 = pd.DataFrame(getPositionEmbedding('Assignment01 [8]_rank', 'A1', d))
    df_2 = pd.DataFrame(getPositionEmbedding('Assignment02 [12]_rank', 'A2', d))
    df_3 = pd.DataFrame(getPositionEmbedding('Assignment03 [25]_rank', 'A3', d))

    # define label
    merge_pd['below 70'] = 0
    merge_pd.loc[merge_pd['Course Grade']<70, 'below 70'] = 1

    # merge the position embedding with the original data
    merge_pd = pd.merge(pd.merge(pd.merge(merge_pd, df_1, on='Assignment01 [8]_rank'), df_2, on='Assignment02 [12]_rank'), df_3, on='Assignment03 [25]_rank')

    col1 =[]
    col2 = []
    col3 = []
    col_all = []
    col1 = df_1.columns.tolist()
    col2 = df_2.columns.tolist()
    col3 = df_3.columns.tolist()
    col_all = np.concatenate([col1, col2, col3])

    # GRU rank
    # Define feature set and target variable
    X = np.array(merge_pd[col_all])

    X = max_abs_scaler.fit_transform(X) 
    Y = np.array(merge_pd['below 70'])


    # Reshape: Shape before reshaping: (486, 150)
    print("Shape before reshaping:", X.shape)
    X = X.reshape(X.shape[0], int(X.shape[1]/df_2.shape[1]), df_2.shape[1]) # Shape after reshaping: (486, 3, 50)
    print("Shape after reshaping:", X.shape)

    # Define the number of folds
    n_folds = 5

    # Define the KFold object
    kfold = KFold(n_splits=n_folds, shuffle=True)

    # Split data into train and test sets
    X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.5, random_state = 42)

    # Define the GRU model
    model = Sequential()
    model.add(GRU(10,  input_shape=(X_train.shape[1], X_train.shape[2])))  # input_shape=(n_timesteps, features)
    model.add(Dense(1, activation='sigmoid'))  # Output layer with sigmoid activation

    # Compile the model
    model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['mae'])

    # Define early stopping criteria
    early_stopping = EarlyStopping(monitor='val_loss', patience=10, restore_best_weights=True)

    # Initialize lists to store the performance metrics
    accuracy_list = []
    precision_list = []
    recall_list = []
    f1_list = []

    # Loop over the folds
    for train_index, test_index in kfold.split(X):
        # Split data into train and test sets
        X_train, X_test = X[train_index], X[test_index]
        y_train, y_test = Y[train_index], Y[test_index]

        # Train the model
        model.fit(X_train, y_train, epochs=4096, batch_size=32, validation_data=(X_test, y_test), callbacks=[early_stopping])

        # Predict the labels for the test set
        y_pred = model.predict(X_test)
        y_pred = (y_pred > 0.5).astype(int)

        # Calculate and print the classification report
        report = classification_report(y_test, y_pred, output_dict=True)

        # Append the performance metrics to the lists
        accuracy_list.append(report['accuracy'])
        precision_list.append(report['macro avg']['precision'])
        recall_list.append(report['macro avg']['recall'])
        f1_list.append(report['macro avg']['f1-score'])
    
    GRU_results.append(np.mean(f1_list))

# 打印结果列表
print(GRU_results)

Shape before reshaping: (486, 15)
Shape after reshaping: (486, 3, 5)
Epoch 1/4096
13/13 [==============================] - 2s 37ms/step - loss: 0.6595 - mae: 0.4788 - val_loss: 0.6552 - val_mae: 0.4764
Epoch 2/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.6321 - mae: 0.4642 - val_loss: 0.6300 - val_mae: 0.4626
Epoch 3/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.6054 - mae: 0.4493 - val_loss: 0.6054 - val_mae: 0.4486
Epoch 4/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.5785 - mae: 0.4336 - val_loss: 0.5794 - val_mae: 0.4331
Epoch 5/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.5508 - mae: 0.4165 - val_loss: 0.5517 - val_mae: 0.4155
Epoch 6/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.5211 - mae: 0.3972 - val_loss: 0.5233 - val_mae: 0.3961
Epoch 7/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.4904 - mae: 0.3760 - val_loss: 0.4960 - val_mae: 0.3759
Epoch 

c:\Users\wyzhw\Documents\GitHub\Desktop\.conda\lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\wyzhw\Documents\GitHub\Desktop\.conda\lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\wyzhw\Documents\GitHub\Desktop\.conda\lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, le

13/13 [==============================] - 0s 5ms/step - loss: 0.3315 - mae: 0.2045 - val_loss: 0.2283 - val_mae: 0.1646
Epoch 3/4096
13/13 [==============================] - 0s 6ms/step - loss: 0.3308 - mae: 0.2040 - val_loss: 0.2281 - val_mae: 0.1650
Epoch 4/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.3298 - mae: 0.2034 - val_loss: 0.2273 - val_mae: 0.1641
Epoch 5/4096
13/13 [==============================] - 0s 6ms/step - loss: 0.3292 - mae: 0.2034 - val_loss: 0.2269 - val_mae: 0.1644
Epoch 6/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.3285 - mae: 0.2026 - val_loss: 0.2259 - val_mae: 0.1634
Epoch 7/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.3277 - mae: 0.2030 - val_loss: 0.2252 - val_mae: 0.1636
Epoch 8/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.3273 - mae: 0.2014 - val_loss: 0.2247 - val_mae: 0.1619
Epoch 9/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.3263 - mae: 0

# Bi-LSTM

In [11]:
# Bi_LSTM rank

Bi_LSTM_results = []

for d in range(5, 1000, 10):

    input_df=pd.read_csv('Student Engagement Level Prediction - Multiclass Case/Student Engagement Level-Multiclass.csv')
    input_p_df=pd.read_csv('Student Performance Prediction - Multiclass Case/Student Performance Prediction-Multi.csv')
    merge_pd = pd.merge(input_df, input_p_df, on='Student ID')

    ''' creat columns called 'Assignment0x [n]_rank' for different assignments '''

    merge_pd['Assignment01 [8]_rank'] = merge_pd['Assignment01 [8]'].rank(ascending=False, method='max').astype(int)
    merge_pd['Assignment02 [12]_rank'] = merge_pd['Assignment02 [12]'].rank(ascending=False, method='max').astype(int)
    merge_pd['Assignment03 [25]_rank'] = merge_pd['Assignment03 [25]'].rank(ascending=False, method='max').astype(int)

    # get the position embedding for each assignment
    df_1 = pd.DataFrame(getPositionEmbedding('Assignment01 [8]_rank', 'A1', d))
    df_2 = pd.DataFrame(getPositionEmbedding('Assignment02 [12]_rank', 'A2', d))
    df_3 = pd.DataFrame(getPositionEmbedding('Assignment03 [25]_rank', 'A3', d))

    # define label
    merge_pd['below 70'] = 0
    merge_pd.loc[merge_pd['Course Grade']<70, 'below 70'] = 1

    # merge the position embedding with the original data
    merge_pd = pd.merge(pd.merge(pd.merge(merge_pd, df_1, on='Assignment01 [8]_rank'), df_2, on='Assignment02 [12]_rank'), df_3, on='Assignment03 [25]_rank')

    col1 =[]
    col2 = []
    col3 = []
    col_all = []
    col1 = df_1.columns.tolist()
    col2 = df_2.columns.tolist()
    col3 = df_3.columns.tolist()
    col_all = np.concatenate([col1, col2, col3])

    # Bi_LSTM rank
    # Define feature set and target variable
    X = np.array(merge_pd[col_all])

    X = max_abs_scaler.fit_transform(X) 
    Y = np.array(merge_pd['below 70'])


    # Reshape: Shape before reshaping: (486, 150)
    print("Shape before reshaping:", X.shape)
    X = X.reshape(X.shape[0], int(X.shape[1]/df_2.shape[1]), df_2.shape[1]) # Shape after reshaping: (486, 3, 50)
    print("Shape after reshaping:", X.shape)

    # Define the number of folds
    n_folds = 5

    # Define the KFold object
    kfold = KFold(n_splits=n_folds, shuffle=True)

    # Split data into train and test sets
    X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.5, random_state = 42)

    # Define the Bi-LSTM model model
    model = Sequential()
    model.add(Bidirectional(LSTM(10, input_shape=(X_train.shape[1], X_train.shape[2]))))# input_shape=(n_timesteps, features)
    model.add(Dense(1, activation='sigmoid'))  # Output layer with sigmoid activation

    # Compile the model
    model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['mae'])

    # Define early stopping criteria
    early_stopping = EarlyStopping(monitor='val_loss', patience=10, restore_best_weights=True)

    # Initialize lists to store the performance metrics
    accuracy_list = []
    precision_list = []
    recall_list = []
    f1_list = []

    # Loop over the folds
    for train_index, test_index in kfold.split(X):
        # Split data into train and test sets
        X_train, X_test = X[train_index], X[test_index]
        y_train, y_test = Y[train_index], Y[test_index]

        # Train the model
        model.fit(X_train, y_train, epochs=4096, batch_size=32, validation_data=(X_test, y_test), callbacks=[early_stopping])

        # Predict the labels for the test set
        y_pred = model.predict(X_test)
        y_pred = (y_pred > 0.5).astype(int)

        # Calculate and print the classification report
        report = classification_report(y_test, y_pred, output_dict=True)

        # Append the performance metrics to the lists
        accuracy_list.append(report['accuracy'])
        precision_list.append(report['macro avg']['precision'])
        recall_list.append(report['macro avg']['recall'])
        f1_list.append(report['macro avg']['f1-score'])
    
    Bi_LSTM_results.append(np.mean(f1_list))

# 打印结果列表
print(Bi_LSTM_results)

Shape before reshaping: (486, 15)
Shape after reshaping: (486, 3, 5)
Epoch 1/4096
13/13 [==============================] - 5s 65ms/step - loss: 0.7079 - mae: 0.5046 - val_loss: 0.7108 - val_mae: 0.5066
Epoch 2/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.6767 - mae: 0.4892 - val_loss: 0.6807 - val_mae: 0.4914
Epoch 3/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.6482 - mae: 0.4743 - val_loss: 0.6527 - val_mae: 0.4762
Epoch 4/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.6202 - mae: 0.4587 - val_loss: 0.6252 - val_mae: 0.4605
Epoch 5/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.5933 - mae: 0.4429 - val_loss: 0.5965 - val_mae: 0.4433
Epoch 6/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.5647 - mae: 0.4251 - val_loss: 0.5666 - val_mae: 0.4242
Epoch 7/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.5352 - mae: 0.4053 - val_loss: 0.5370 - val_mae: 0.4037
Epoch 

c:\Users\wyzhw\Documents\GitHub\Desktop\.conda\lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\wyzhw\Documents\GitHub\Desktop\.conda\lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\wyzhw\Documents\GitHub\Desktop\.conda\lib\site-packages\sklearn\metrics\_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, le

13/13 [==============================] - 0s 5ms/step - loss: 0.2793 - mae: 0.1905 - val_loss: 0.2274 - val_mae: 0.1716
Epoch 3/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.2687 - mae: 0.1812 - val_loss: 0.2169 - val_mae: 0.1615
Epoch 4/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.2582 - mae: 0.1720 - val_loss: 0.2107 - val_mae: 0.1545
Epoch 5/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.2515 - mae: 0.1630 - val_loss: 0.2036 - val_mae: 0.1457
Epoch 6/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.2460 - mae: 0.1565 - val_loss: 0.2016 - val_mae: 0.1430
Epoch 7/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.2419 - mae: 0.1527 - val_loss: 0.2011 - val_mae: 0.1415
Epoch 8/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.2415 - mae: 0.1566 - val_loss: 0.2055 - val_mae: 0.1466
Epoch 9/4096
13/13 [==============================] - 0s 5ms/step - loss: 0.2348 - mae: 0

In [12]:
Bi_LSTM_results

[0.6291237065872973,
 0.779512441357164,
 0.7617201801065235,
 0.7877318667354529,
 0.7307057451882093,
 0.7865321767091513,
 0.7795663341380829,
 0.8020882042360867,
 0.7889974858209066,
 0.7806199720109784,
 0.7897970114754781,
 0.7651791034396561,
 0.8202511306069342,
 0.787302392008911,
 0.7680324187118254,
 0.8184267924035649,
 0.7593794060912848,
 0.7901267584229636,
 0.7742553704993445,
 0.7621019998715968,
 0.8014249522881765,
 0.7847270274016622,
 0.7787872613109448,
 0.7851428196432828,
 0.7868105540532536,
 0.7841998747809485,
 0.7601879997941146,
 0.7904185610619964,
 0.7780128522877676,
 0.7687691394061241,
 0.8037836141297229,
 0.7882961528381239,
 0.8704825745460216,
 0.827805516285783,
 0.7926268046615025,
 0.7509539982566515,
 0.772309901724918,
 0.7833573370243692,
 0.7614923439808683,
 0.7636444390190371,
 0.7989396176586946,
 0.801805747697024,
 0.7788281941155202,
 0.7652455605438212,
 0.791874187160839,
 0.7939836136316902,
 0.7686183963409042,
 0.8009790759422266

In [13]:
data = [LR_results, SVM_results, MLP_results, RNN_results, LSTM_results, GRU_results, Bi_LSTM_results]
df = pd.DataFrame(data=data, index=['LR', 'SVM', 'MLP', 'RNN', 'LSTM', 'GRU', 'Bi_LSTM'], columns=range(5, 1000, 10))
df

5         15        25        35        45        55        65   \
LR       0.484277  0.616016  0.614660  0.573599  0.531795  0.527891  0.557663   
SVM      0.474045  0.574791  0.594185  0.590697  0.596152  0.588880  0.597054   
MLP      0.518017  0.616550  0.574579  0.571255  0.548766  0.553354  0.584639   
RNN      0.592330  0.775248  0.776433  0.794461  0.808504  0.776178  0.790115   
LSTM     0.697086  0.804376  0.751445  0.789244  0.836597  0.788535  0.815375   
GRU      0.640010  0.806996  0.784462  0.786127  0.792833  0.810083  0.780156   
Bi_LSTM  0.629124  0.779512  0.761720  0.787732  0.730706  0.786532  0.779566   

              75        85        95   ...       905       915       925  \
LR       0.529770  0.527103  0.518319  ...  0.501382  0.500128  0.499649   
SVM      0.590074  0.596431  0.593715  ...  0.592442  0.592442  0.592442   
MLP      0.548347  0.558953  0.545076  ...  0.538315  0.550356  0.543940   
RNN      0.757243  0.769308  0.752803  ...  0.769074  0.817904  0.746642   
LSTM     0.834772  0.782833  0.768972  ...  0.780014  0.783565  0.779229   
GRU      0.810801  0.775654  0.771544  ...  0.828112  0.815690  0.802243   
Bi_LSTM  0.802088  0.788997  0.780620  ...  0.753976  0.766131  0.777649   

              935       945       955       965       975       985       995  
LR       0.499649  0.498657  0.499649  0.496970  0.497222  0.498214  0.499649  
SVM      0.592442  0.592442  0.592442  0.592442  0.592442  0.592442  0.592442  
MLP      0.541679  0.546833  0.566459  0.551154  0.552134  0.546541  0.538404  
RNN      0.825604  0.821394  0.818186  0.839010  0.810231  0.808565  0.766837  
LSTM     0.818974  0.782991  0.800125  0.844019  0.760194  0.828427  0.737772  
GRU      0.808704  0.834037  0.789214  0.831624  0.801626  0.842146  0.797351  
Bi_LSTM  0.813731  0.835673  0.771691  0.784396  0.798839  0.807901  0.793270  

[7 rows x 100 columns]

In [14]:
# save the dataframe as a csv file, specify the file name as "data.csv"
df.to_csv("data.csv")

# plot

In [15]:
d_list

NameError: name 'd_list' is not defined

In [ ]:
# 导入plotly库
import plotly.graph_objects as go

# 创建一个空白的图形对象
fig = go.Figure()

d_list = []
for d in range(5, 1000, 10):
    d_list.append(d)

columns = d_list

# 添加各个模型的曲线，指定x轴、y轴、颜色和标签
fig.add_trace(go.Scatter(x=d_list, y=LR_results, mode='lines', line=dict(color='red'), name='LR'))
fig.add_trace(go.Scatter(x=d_list, y=SVM_results, mode='lines', line=dict(color='blue'), name='SVM'))
fig.add_trace(go.Scatter(x=d_list, y=MLP_results, mode='lines', line=dict(color='green'), name='MLP'))
fig.add_trace(go.Scatter(x=d_list, y=RNN_results, mode='lines', line=dict(color='cyan'), name='RNN'))
fig.add_trace(go.Scatter(x=d_list, y=LSTM_results, mode='lines', line=dict(color='magenta'), name='LSTM'))
fig.add_trace(go.Scatter(x=d_list, y=GRU_results, mode='lines', line=dict(color='yellow'), name='GRU'))
fig.add_trace(go.Scatter(x=d_list, y=Bi_LSTM_results , mode='lines', line=dict(color='black'), name='Bi-LSTM'))


# 设置标题和坐标轴标签
fig.update_layout(title="Model Performance vs d value", xaxis_title="d value", yaxis_title="Model Performance")

# 调整图例位置和大小
fig.update_layout(legend=dict(
    orientation="h",
    yanchor="bottom",
    y=1.02,
    xanchor="right",
    x=1
))

# 显示图形
fig.show()

In [25]:
# 导入plotly库
import plotly.graph_objects as go

# 创建一个空白的图形对象
fig = go.Figure()

d_list = []
for d in range(5, 1000, 10):
    d_list.append(d)

columns = d_list

# 添加各个模型的曲线，指定x轴、y轴、颜色和标签
fig.add_trace(go.Scatter(x=d_list, y=LR_results, mode='lines', line=dict(color='red'), name='LR'))
fig.add_trace(go.Scatter(x=d_list, y=SVM_results, mode='lines', line=dict(color='blue'), name='SVM'))
fig.add_trace(go.Scatter(x=d_list, y=MLP_results, mode='lines', line=dict(color='green'), name='MLP'))
fig.add_trace(go.Scatter(x=d_list, y=RNN_results, mode='lines', line=dict(color='cyan'), name='RNN'))
fig.add_trace(go.Scatter(x=d_list, y=LSTM_results, mode='lines', line=dict(color='magenta'), name='LSTM'))
fig.add_trace(go.Scatter(x=d_list, y=GRU_results, mode='lines', line=dict(color='yellow'), name='GRU'))
fig.add_trace(go.Scatter(x=d_list, y=Bi_LSTM_results , mode='lines', line=dict(color='black'), name='Bi-LSTM'))


# 设置标题和坐标轴标签
fig.update_layout(title="Model Performance vs d value", xaxis_title="d value", yaxis_title="F1_Score (below 70)")

# 调整图例位置和大小
fig.update_layout(legend=dict(
    orientation="h",
    yanchor="bottom",
    y=1.02,
    xanchor="right",
    x=1
))

fig.update_layout(width=800, height=600)

# 显示图形
fig.show()

In [18]:
import pandas as pd
import plotly.graph_objects as go

# 创建一个dataframe
df = pd.DataFrame({
    "F1_macro": ["LR", "SVM", "MLP", "RNN", "LSTM", "GRU", "Bi-LSTM"],
    "Score": [0.7587, 0.7562, 0.7612, 0.7716, 0.7754, 0.7548, 0.7740],
    "Rank(d=5)": [0.5845, 0.5933, 0.6011, 0.6538, 0.6732, 0.6832, 0.6765],
    "Rank(d=10)": [0.7136, 0.7391, 0.7032, 0.7966, 0.8010, 0.8053, 0.8078],
    "Rank(d=50)": [0.5979, 0.7263, 0.6367, 0.8263, 0.8164, 0.8182, 0.8105],
    "Rank(d=100)": [0.5525, 0.7112, 0.6158, 0.8097, 0.8018, 0.8128, 0.8047],
    "Rank(Max)": [0.7152, 0.7251, 0.6643, 0.8585, 0.8650, 0.8563, 0.8811]
})

# 创建一个图表对象
fig = go.Figure()

# 添加柱状图，表示Score列的值
fig.add_trace(go.Bar(x=df["F1_macro"], y=df["Score"], name="Score"))

# 添加折线图，表示不同d值下的Rank列的值
fig.add_trace(go.Scatter(x=df["F1_macro"], y=df["Rank(d=5)"], mode="lines+markers", name="Rank(d=5)"))
fig.add_trace(go.Scatter(x=df["F1_macro"], y=df["Rank(d=10)"], mode="lines+markers", name="Rank(d=10)"))
fig.add_trace(go.Scatter(x=df["F1_macro"], y=df["Rank(d=50)"], mode="lines+markers", name="Rank(d=50)"))
fig.add_trace(go.Scatter(x=df["F1_macro"], y=df["Rank(d=100)"], mode="lines+markers", name="Rank(d=100)"))
fig.add_trace(go.Scatter(x=df["F1_macro"], y=df["Rank(Max)"], mode="lines+markers", name="Rank(Best Result)"))

# 设置y轴的范围和标签
fig.update_yaxes(range=[0,1], title_text="Value")

# 设置图表的标题和布局
fig.update_layout(title_text="Model Comparison", barmode="group", xaxis_title="model", yaxis_title="f1_score")


fig.update_layout(width=600, height=400)

# 显示图表
fig.show()
